# SETUP

In [ ]:
from google.colab import drive
import os

drive.mount('/content/gdrive')

!ls
%cd /content/gdrive/MyDrive/rajat.bans/RAG/
# !pip install -r requirements.txt

In [ ]:
%reload_ext autoreload
%autoreload 2
%load rag.py
import rag

# DB PREPARATION

In [ ]:
import pandas as pd
from langchain_community.embeddings import HuggingFaceEmbeddings
df = pd.read_csv('./data/149_adclick_Jun_facty_activeBeat_Health_dupRemoved0.85_campaign.tsv', sep='\t')
# df.dropna(axis=0, how='any', inplace=True)
# df.drop_duplicates(subset = ['ad_title', 'ad_desc'], inplace=True)

# -------------------------------
# ADS DATA PREPROCESSING
dfRPC = df[df['RPC'] > 0]
dfRPC = dfRPC.dropna()
dfCampaign = df[df['type'] == 'campaign']
dfCampaign = dfCampaign.fillna('')
df = pd.concat([dfRPC, dfCampaign])
df

content = (df["ad_title"] + ". " + df["ad_desc"]).tolist()
metadata = [
        {"publisher_url": row["publisher_url"], "keyword_term": row["keyword_term"], "ad_display_url": row["ad_display_url"], "revenue": row["revenue"], "ad_click_count": row["ad_click_count"], "RPC": row["RPC"], "Type": row["type"]}
        # {"revenue": row["revenue"], "ad_click_count": row["ad_click_count"]}
        for _, row in df.iterrows()
    ]

# --------------------------------
# WEB DATA PROCESSING
# from urllib.parse import urlparse
# import re
# def get_cleaned_url(url):
#     path = urlparse(url).path.strip()
#     cleaned_path = re.sub(r'[^a-zA-Z0-9\s-]', ' ', path).replace('/', '')
#     cleaned_path = re.sub(r'[^a-zA-Z0-9\s]', ' ', path).replace('-', '')
#     return cleaned_path.strip()

# df['cleaned_url'] = df['url'].map(get_cleaned_url)
# df.dropna(subset=['cleaned_url', 'url_content', 'url_title'], inplace=True)
# df['combined'] = df['cleaned_url'] + ". " + df['url_title'] + ". " + df['url_content']
# content = df["combined"].tolist()
# metadata = [
#         {"title": row["url_title"], "url": row["url"]}
#         for _, row in df.iterrows()
#     ]

embeddings_hf = HuggingFaceEmbeddings(model_name="BAAI/bge-m3", show_progress = True)
faiss_db = rag.FAISS_DB()
docs = faiss_db.createDocs(content, metadata)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Documents are split into 15550 passages


In [ ]:
print(len(docs), docs[0], docs[len(docs)-1])
db = faiss_db.createDBFromDocs(docs, embeddings_hf)
faiss_db.saveDB(db, './vectorstore/db_faiss_ads_Jun_facty_activebeat_Health_dupRemoved0.85')

(15550,
 Document(metadata={'publisher_url': '', 'keyword_term': '', 'ad_display_url': '', 'revenue': '', 'ad_click_count': '', 'RPC': '', 'Type': 'campaign'}, page_content="How To Bring High Blood Pressure Down Fast. This safe, natural solution doesn't just treat hypertension but actually corrects it!"))

In [ ]:
# # ************************************************************************
# # PARALLELY CREATING DB - BACKUP FOR FUTURE USE
# import time
# import threading
# import os
# one_db_docs_size = 1000
# starting_i = 0
# parallel_processes = 3
# def split_list(lst, n):
#     k, m = divmod(len(lst), n)
#     return (lst[i * k + min(i, m):(i + 1) * k + min(i + 1, m)] for i in range(n))
# def createDBForIndexes(inds):
#     for i in inds:
#         ctime = time.time()
#         print(f"Processing {i}")
#         if not os.path.exists(DB_FAISS_PATH + "/index_{int(i/one_db_docs_size)}.faiss"):
#             db = FAISS.from_documents(split_docs[i:i+one_db_docs_size], embeddings_hf)
#             db.save_local(DB_FAISS_PATH, index_name = f"index_{int(i/one_db_docs_size)}")
#         ctime = time.time() - ctime
#         print(f"{i})Time taken", ctime)
# indexes = split_list(range(starting_i, len(split_docs), one_db_docs_size), parallel_processes)
# threads = []
# for i, one_process_indexes in enumerate(indexes):
#     thread = threading.Thread(target=createDBForIndexes, args=(one_process_indexes,))
#     thread.start()
#     threads.append(thread)
# for thread in threads:
#     thread.join()
# print("All threads completed.")
# # ************************************************************************

# PROCESSING ADS TO FORM QNA FOR URLS

In [ ]:
import pandas as pd
import rag
helper = rag.Helper(
        "./vectorstore/db_faiss_ads_Jun_facty_activebeat_Health_dupRemoved0.85"
    )

data = pd.read_csv("./data/148_facty_activebeat_24Jun-30Jun_top1000each_urlsContent.tsv", sep="\t")
data = data.dropna(axis=0, how="any", inplace=True)
# data.drop_duplicates(subset = ['ad_title', 'ad_desc'], inplace=True)
data["core_content"] = data.apply(lambda row: (
    "Page Title -: " 
    + row["url_title"] 
    + "\nPage Content -: " 
    + ". ".join(row["url_content"].split(". ")[:7])
), axis=1)

total_cost = 0
data

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


domain_name                                       stripped_url  \
0     activebeat.com  https://activebeat.com/your-health/10-warning-...   
1     activebeat.com  https://activebeat.com/your-health/women/14-ea...   
2     activebeat.com  https://activebeat.com/your-health/chronic-kid...   
3     activebeat.com  https://activebeat.com/health-news/15-foods-to...   
4     activebeat.com  https://activebeat.com/your-health/7-symptoms-...   
...              ...                                                ...   
1938       facty.com  https://facty.com/conditions/alzheimers/10-sym...   
1939       facty.com  https://facty.com/network/life/the-top-30-wors...   
1940       facty.com  https://facty.com/ailments/kidney/10-causes-of...   
1941       facty.com  https://facty.com/conditions/muscular/10-home-...   
1942       facty.com  https://facty.com/conditions/myasthenia-gravis...   

      kwd_imp kwd_click ad_click     revenue  rank  \
0     447,234    10,129    5,750  $14,749.43     1   
1     276,507     3,643    1,957   $4,334.21     2   
2     187,361     3,722    2,301   $1,601.17     3   
3     183,504     4,605    2,173   $4,567.85     4   
4     178,560     2,008    1,102     $546.59     5   
...       ...       ...      ...         ...   ...   
1938    3,209        13        4       $3.13   996   
1939    3,208        14        3       $0.41   997   
1940    3,199        31       13       $2.39   998   
1941    3,194        60       37       $6.46   999   
1942    3,192        68       46      $10.16  1000   

                                              url_title  \
0              Lung Cancer: 22 Early Signs and Symptoms   
1       14 Early Signs of Cancer Women Shouldn’t Ignore   
2     Chronic Kidney Disease: 20 Common Symptoms of CKD   
3                      15 Foods to Help Manage Diabetes   
4                  Signs and Symptoms of Kidney Failure   
...                                                 ...   
1938  The Early Signs and Symptoms of Lewy Body Deme...   
1939  The Top 30 Worst Places to Live in the United ...   
1940       10 Causes of Kidney Infection - Facty Health   
1941  Can These 15 Home Treatments Help Your Restles...   
1942    10 Symptoms of Myasthenia Gravis - Facty Health   

                                            url_content  \
0     Lung Cancer: 22 Early Signs and Symptoms. Lung...   
1     14 Early Signs of Cancer Women Shouldn’t Ignor...   
2     Chronic Kidney Disease: 20 Common Symptoms of ...   
3     15 Foods to Help Manage Diabetes. Being diagno...   
4     Signs and Symptoms of Kidney Failure. Many peo...   
...                                                 ...   
1938  8 . Loss of Balance. It is common for Lewy bod...   
1939  Updated: Nov 9, 2022. 10 . Idabel, OK. Small-t...   
1940  10 Causes of Kidney Infection. A kidney infect...   
1941  Can These 15 Home Treatments Help Your Restles...   
1942  10 Symptoms of Myasthenia Gravis. Myasthenia g...   

                                           core_content  
0     Page Title -: Lung Cancer: 22 Early Signs and ...  
1     Page Title -: 14 Early Signs of Cancer Women S...  
2     Page Title -: Chronic Kidney Disease: 20 Commo...  
3     Page Title -: 15 Foods to Help Manage Diabetes...  
4     Page Title -: Signs and Symptoms of Kidney Fai...  
...                                                 ...  
1938  Page Title -: The Early Signs and Symptoms of ...  
1939  Page Title -: The Top 30 Worst Places to Live ...  
1940  Page Title -: 10 Causes of Kidney Infection - ...  
1941  Page Title -: Can These 15 Home Treatments Hel...  
1942  Page Title -: 10 Symptoms of Myasthenia Gravis...  

[1943 rows x 10 columns]

In [ ]:
import pandas as pd
responses_file_name = './data/150_results_facty_activebeat_24Jun-30Jun_top1000each_urlsContent.tsv'
try:
    responses = pd.read_csv(responses_file_name, sep='\t')
except FileNotFoundError:
    responses = pd.DataFrame()

new_rows = []
for i in range(len(responses), len(data)):
    print(i, end = ',')
    row = data.iloc[i, :]
    try:
        answer = {
            'domain_name': row['domain_name'],
            'url': row['stripped_url'],
            #   'input': '. '.join(row['stripped_url'].split('/')[3:]),
            'kwd_imp': row['kwd_imp'],
            'kwd_click': row['kwd_click'],
            'ad_click': row['ad_click'],
            'revenue': row['revenue'],
            'rank': row['rank'],
            'url_title': row['url_title'],
            'url_content': row['url_content'],
            'input': row['core_content'],
        }

        reply, clustered_docs = my_rag.getRagResponse(row['core_content'])
        answer["relation_reasoning"] = reply['relation_answer']['reasoning']
        answer["relation_classification"] = reply['relation_answer']['classification']
        answer["relation_tokens_used"] = reply['tokens_used_relation']

        answer["reasoning"] = reply['question_answer']['reasoning']
        answer["question"] = reply['question_answer']['question']
        options = reply['question_answer']['options']
        options_res = ""
        for option in options:
            options_res += option + "\n"
            for ad in options[option]:
                options_res += ad + "\n"
            options_res += "\n"
        answer["options"] = options_res
        answer["options_count"] = str(len(options))
        answer["question_tokens_used"] = reply['tokens_used_question']

        ads_data = ""
        for ind, cluster in enumerate(clustered_docs):
            ads_data += f"*************** Cluster-:{ind+1} **************\n"
            for doc in cluster:
                ad = doc[0]
                ads_data += ad.page_content + "\n"
                ads_data += "publisher_url: " + ad.metadata['publisher_url'] + " | "
                ads_data += "keyword_term: " + ad.metadata['keyword_term'] + " | "
                ads_data += "ad_display_url: " + ad.metadata['ad_display_url'] + " | "
                ads_data += "revenue: " + str(ad.metadata['revenue']) + " | "
                ads_data += "ad_click_count: " + str(ad.metadata['ad_click_count']) + " | "
                ads_data += "RPC: " + str(ad.metadata['RPC']) + " | "
                ads_data += "Type: " + ad.metadata['Type'] + "\n"
                ads_data += "Value: " + str(doc[1]) + "\n"
                ads_data += "\n"
            ads_data += "\n"
        answer["ads_data"] = ads_data

        cost = (answer["relation_tokens_used"] + answer["question_tokens_used"]) * 0.6/1000000
        total_cost += cost
        answer['cost'] = float(cost)
    except Exception as e:
        print(e)
    new_rows.append(answer)

    if i % 10 == 0:
        print(" Total cost is up to now is", total_cost)
        responses = pd.concat([responses, pd.DataFrame(new_rows)], ignore_index=True)
        responses.to_csv(responses_file_name, sep='\t', index=False)
        new_rows = []

responses = pd.concat([responses, pd.DataFrame(new_rows)], ignore_index=True)
responses.to_csv(responses_file_name, sep='\t', index=False)
responses


31,32,33,34,35,36,37,38,39,40, Total cost is up to now is 0.07723840000000001
41,42,43,44,45,46,47,48,49,50, Total cost is up to now is 0.09258700000000002
51,52,53,54,55,56,57,58,59,60, Total cost is up to now is 0.10775680000000001
61,62,63,64,65,66,67,68,69,70, Total cost is up to now is 0.12251020000000001
71,72,73,74,75,76,77,78,79,80, Total cost is up to now is 0.13763380000000003
81,82,83,84,85,86,87,88,89,90, Total cost is up to now is 0.1530052
91,92,93,94,95,96,97,98,99,100, Total cost is up to now is 0.1679824
101,102,103,104,105,106,107,108,109,110, Total cost is up to now is 0.18317620000000004
111,112,113,114,115,116,117,118,119,120, Total cost is up to now is 0.19802140000000004
121,122,123,124,125,126,127,128,129,130, Total cost is up to now is 0.212821
131,132,133,134,135,136,137,138,139,140, Total cost is up to now is 0.22768839999999999
141,142,143,144,145,146,147,148,149,150, Total cost is up to now is 0.24157479999999998
151,152,153,154,155,156,157,158,159,160, Tot

domain_name                                                url  \
0     activebeat.com  https://activebeat.com/your-health/10-warning-...   
1     activebeat.com  https://activebeat.com/your-health/women/14-ea...   
2     activebeat.com  https://activebeat.com/your-health/chronic-kid...   
3     activebeat.com  https://activebeat.com/health-news/15-foods-to...   
4     activebeat.com  https://activebeat.com/your-health/7-symptoms-...   
...              ...                                                ...   
1938       facty.com  https://facty.com/conditions/alzheimers/10-sym...   
1939       facty.com  https://facty.com/network/life/the-top-30-wors...   
1940       facty.com  https://facty.com/ailments/kidney/10-causes-of...   
1941       facty.com  https://facty.com/conditions/muscular/10-home-...   
1942       facty.com  https://facty.com/conditions/myasthenia-gravis...   

      kwd_imp kwd_click ad_click     revenue  rank  \
0     447,234    10,129    5,750  $14,749.43     1   
1     276,507     3,643    1,957   $4,334.21     2   
2     187,361     3,722    2,301   $1,601.17     3   
3     183,504     4,605    2,173   $4,567.85     4   
4     178,560     2,008    1,102     $546.59     5   
...       ...       ...      ...         ...   ...   
1938    3,209        13        4       $3.13   996   
1939    3,208        14        3       $0.41   997   
1940    3,199        31       13       $2.39   998   
1941    3,194        60       37       $6.46   999   
1942    3,192        68       46      $10.16  1000   

                                              url_title  \
0              Lung Cancer: 22 Early Signs and Symptoms   
1       14 Early Signs of Cancer Women Shouldn’t Ignore   
2     Chronic Kidney Disease: 20 Common Symptoms of CKD   
3                      15 Foods to Help Manage Diabetes   
4                  Signs and Symptoms of Kidney Failure   
...                                                 ...   
1938  The Early Signs and Symptoms of Lewy Body Deme...   
1939  The Top 30 Worst Places to Live in the United ...   
1940       10 Causes of Kidney Infection - Facty Health   
1941  Can These 15 Home Treatments Help Your Restles...   
1942    10 Symptoms of Myasthenia Gravis - Facty Health   

                                            url_content  \
0     Lung Cancer: 22 Early Signs and Symptoms. Lung...   
1     14 Early Signs of Cancer Women Shouldn’t Ignor...   
2     Chronic Kidney Disease: 20 Common Symptoms of ...   
3     15 Foods to Help Manage Diabetes. Being diagno...   
4     Signs and Symptoms of Kidney Failure. Many peo...   
...                                                 ...   
1938  8 . Loss of Balance. It is common for Lewy bod...   
1939  Updated: Nov 9, 2022. 10 . Idabel, OK. Small-t...   
1940  10 Causes of Kidney Infection. A kidney infect...   
1941  Can These 15 Home Treatments Help Your Restles...   
1942  10 Symptoms of Myasthenia Gravis. Myasthenia g...   

                                                  input  \
0     Page Title -: Lung Cancer: 22 Early Signs and ...   
1     Page Title -: 14 Early Signs of Cancer Women S...   
2     Page Title -: Chronic Kidney Disease: 20 Commo...   
3     Page Title -: 15 Foods to Help Manage Diabetes...   
4     Page Title -: Signs and Symptoms of Kidney Fai...   
...                                                 ...   
1938  Page Title -: The Early Signs and Symptoms of ...   
1939  Page Title -: The Top 30 Worst Places to Live ...   
1940  Page Title -: 10 Causes of Kidney Infection - ...   
1941  Page Title -: Can These 15 Home Treatments Hel...   
1942  Page Title -: 10 Symptoms of Myasthenia Gravis...   

                                     relation_reasoning  \
0     First retreived document value less than thres...   
1     First retreived document value less than thres...   
2     First retreived document value less than thres...   
3     First retreived document value less than thres...   
4     First retreived document value 

In [ ]:
import pandas as pd
df = pd.read_csv('./data/150_results_facty_activebeat_24Jun-30Jun_top1000each_urlsContent.tsv', sep='\t')
df = df[(df['options_count'] < 5) & (df['options_count'] > 1)].loc[:, ['url', 'question', 'options']].dropna(how='any')

def get_data(row):
    res = []
    res.append([row['url'], row['question'], 1, 1])
    options = [option.split("\n")[0] for option in row['options'].split("\n\n")]
    for ind, option in enumerate(options):
        if(option != ""):
            res.append([row['url'], ". ".join(option.split(". ")[1:]), ind+2, 0])
    return res

results = [item for sublist in df.apply(get_data, axis=1) for item in sublist]
df2 = pd.DataFrame(results, columns=['url', 'keyword', 'rank', 'is_question'])
df2.to_csv('./data/151_url_keyword_rank_150data.tsv', sep='\t', index=False)
df2


url  \
0     https://activebeat.com/your-health/10-warning-...   
1     https://activebeat.com/your-health/10-warning-...   
2     https://activebeat.com/your-health/10-warning-...   
3     https://activebeat.com/your-health/10-warning-...   
4     https://activebeat.com/your-health/women/14-ea...   
...                                                 ...   
6049  https://facty.com/conditions/muscular/10-home-...   
6050  https://facty.com/conditions/muscular/10-home-...   
6051  https://facty.com/conditions/myasthenia-gravis...   
6052  https://facty.com/conditions/myasthenia-gravis...   
6053  https://facty.com/conditions/myasthenia-gravis...   

                                            keyword  rank  is_question  
0       Concerned about early signs of lung cancer?     1            1  
1                      Symptoms and Early Detection     2            0  
2                        Early Diagnosis Importance     3            0  
3                          Awareness and Prevention     4            0  
4     Concerned about early signs of breast cancer?     1            1  
...                                             ...   ...          ...  
6049                         Leg Swelling Home Care     3            0  
6050               Restless Legs Syndrome Solutions     4            0  
6051    Concerned about Myasthenia Gravis symptoms?     1            1  
6052              Learn about Fibromyalgia Symptoms     2            0  
6053         Learn about Myasthenia Gravis Symptoms     3            0  

[6054 rows x 4 columns]